In [4]:
import torch
import numpy as np 
import pandas as pd 

# check if CUDA is available
train_on_gpu = torch.cuda.is_available()

if not train_on_gpu:
    print('CUDA is not available.  Training on CPU ...')
else:
    print('CUDA is available!  Training on GPU ...')

CUDA is not available.  Training on CPU ...


In [5]:
data = pd.read_csv('train.csv')

labels = data['label'] 
features = data.drop('label', axis = 1)

In [6]:
features = torch.from_numpy(features.values.reshape(-1,1,28,28))
features = features.type(torch.float32)

labels = torch.from_numpy(labels.values)
labels = labels.type(torch.long)

In [7]:
from torchvision import datasets
from torch.utils.data.sampler import SubsetRandomSampler
from torch.utils.data import TensorDataset

train_data = TensorDataset(features, labels)

idx = list(range(len(train_data)))
mid = int(0.9*len(train_data))

# split and suffle indexes
train_idx = SubsetRandomSampler(idx[:mid])
test_idx = SubsetRandomSampler(idx[mid:])

# data loaders
train_loader = torch.utils.data.DataLoader(train_data, batch_size=20, sampler=train_idx)
test_loader = torch.utils.data.DataLoader(train_data, batch_size=20, sampler=test_idx)


In [8]:
print(len(train_loader)*20)
print(len(test_loader)*20)

37800
4200


In [10]:
import torch.nn as nn
import torch.nn.functional as F

# define the NN architecture
class Net_1(nn.Module):
    def __init__(self):
        super(Net_1, self).__init__()        
        self.fc1 = nn.Linear(28 * 28, 512)
        self.fc2 = nn.Linear(512, 512)
        self.fc3 = nn.Linear(512, 10)
        self.dropout = nn.Dropout(0.2)
    def forward(self, x):
        # flatten image input
        x = x.view(-1, 28 * 28)
        x = F.relu(self.fc1(x))
        x = self.dropout(x)
        x = F.relu(self.fc2(x))
        x = self.dropout(x)   
        x = F.log_softmax(self.fc3(x), dim=1)
        return x
model_1 = Net_1()
print(model_1)

Net_1(
  (fc1): Linear(in_features=784, out_features=512, bias=True)
  (fc2): Linear(in_features=512, out_features=512, bias=True)
  (fc3): Linear(in_features=512, out_features=10, bias=True)
  (dropout): Dropout(p=0.2)
)


In [11]:
import torch.nn as nn
import torch.nn.functional as F

# define the NN architecture
class Net_2(nn.Module):
    def __init__(self):
        super(Net_2, self).__init__()        
        self.fc1 = nn.Linear(28 * 28, 512)
        self.fc3 = nn.Linear(512, 10)
        self.dropout = nn.Dropout(0.2)
    def forward(self, x):
        # flatten image input
        x = x.view(-1, 28 * 28)
        x = F.relu(self.fc1(x))
        x = self.dropout(x)   
        x = F.log_softmax(self.fc3(x), dim=1)
        return x
model_2 = Net_2()
print(model_2)

Net_2(
  (fc1): Linear(in_features=784, out_features=512, bias=True)
  (fc3): Linear(in_features=512, out_features=10, bias=True)
  (dropout): Dropout(p=0.2)
)


In [23]:
import torch.nn as nn
import torch.nn.functional as F

# define the NN architecture
class Net_3(nn.Module):
    def __init__(self):
        super(Net_3, self).__init__()        
        self.fc1 = nn.Linear(20, 10)
        self.dropout = nn.Dropout(0.2)
    def forward(self, x):
        # flatten image input
        x = x.view(-1, 20)
        x = self.dropout(x)   
        x = F.log_softmax(self.fc1(x), dim=1)
        return x
model_3 = Net_3()
print(model_3)

Net_3(
  (fc1): Linear(in_features=20, out_features=10, bias=True)
  (dropout): Dropout(p=0.2)
)


In [27]:
# loss function
criterion_1 = nn.CrossEntropyLoss()
criterion_2 = nn.CrossEntropyLoss()
criterion_3 = nn.CrossEntropyLoss()

# optimizer
optimizer_1 = torch.optim.Adagrad(model_1.parameters(), lr=0.001)
optimizer_2 = torch.optim.Adagrad(model_2.parameters(), lr=0.001)
optimizer_3 = torch.optim.Adagrad(model_3.parameters(), lr=0.001)

In [ ]:
# number of epochs 
epochs = 1

model_1.train() 
model_2.train()
model_3.train()

for epoch in range(epochs):
    
    train_loss = 0.0
    total = 0.0
    
    for data, target in train_loader:
        optimizer_1.zero_grad()
        optimizer_2.zero_grad()
        optimizer_3.zero_grad()
        
        output_1 = model_1(data)
        output_2 = model_2(data)
        output = torch.cat((output_1, output_2), 1)
        output_3 = model_3(output)
        
        loss_3 = criterion_3(output, target)
        back_to_MLP1_MLP2 = output-loss_3/model_3.state_dict()['fc1.weight'].mean(0)
        back_to_MLP1 = back_to_MLP1_MLP2[:,:10]
        
        print(back_to_MLP1_MLP2)
        print("**************************")
        print(back_to_MLP1)
        

tensor([[   227.3468,  -1992.8104,    437.1429,  -1008.0478,  -1015.2155,
            175.1681,   -922.5182,   -792.4646,   -241.0813,  -1116.4131,
           -456.8893,   -675.1517,    466.1257,    601.7843,   -317.3050,
         -31966.5352,    301.3075,    264.8430,   2409.0376, -14733.0518],
        [   231.7881,  -1993.8611,    422.6231,  -1006.1074,  -1012.7399,
            193.8565,   -936.8801,   -786.5222,   -247.8715,  -1095.2739,
           -479.2070,   -679.8809,    467.1953,    631.8527,   -324.4747,
         -31980.1074,    300.3226,    284.4990,   2383.9517, -14737.5977],
        [   221.6040,  -2000.4379,    406.7329,  -1012.2766,  -1015.2483,
            171.4193,   -939.9637,   -800.9145,   -238.3968,  -1119.0740,
           -455.9929,   -734.8589,    433.9167,    577.1072,   -419.9639,
         -31937.1621,    245.2671,    228.7591,   2339.2637, -14766.8623],
        [   229.6254,  -1997.2874,    427.8630,  -1005.8716,   -996.3870,
            179.8972,   -936.1223, 

       grad_fn=<SliceBackward>)
tensor([[   216.2621,  -1841.3273,    390.0591,   -932.4150,   -930.6590,
            169.4496,   -856.2385,   -725.0828,   -219.4154,  -1014.4869,
           -428.5237,   -590.2914,    442.2101,    574.0271,   -327.2523,
         -29401.8047,    323.2131,    247.0537,   2195.4111, -13565.5479],
        [   201.3261,  -1841.2632,    387.7897,   -929.8773,   -941.5274,
            174.3603,   -855.3770,   -725.7201,   -219.4305,  -1024.3212,
           -421.1757,   -617.7452,    435.4487,    552.7289,   -267.2703,
         -29405.1094,    281.6639,    237.5200,   2209.3862, -13551.9033],
        [   222.6453,  -1833.2903,    394.8784,   -941.6062,   -937.8394,
            175.5894,   -862.7110,   -722.9561,   -227.3660,  -1016.2260,
           -477.7118,   -665.4088,    398.5679,    513.9025,   -309.4195,
         -29394.2539,    243.5138,    202.4427,   2153.8535, -13572.3818],
        [   209.4553,  -1833.2365,    386.4991,   -937.6795,   -930.0274,
   

       grad_fn=<SliceBackward>)
tensor([[   219.5706,  -1947.1492,    412.2938,   -986.6598,   -988.5399,
            177.1086,   -900.3578,   -776.9797,   -237.4486,  -1074.8799,
           -452.7453,   -665.9902,    473.4819,    561.5184,   -306.7970,
         -31233.7598,    300.2741,    286.3855,   2330.5911, -14408.4512],
        [   213.5238,  -1947.1335,    412.6436,  -1010.1702,   -985.2010,
            167.2534,   -909.2557,   -783.0089,   -259.8085,  -1069.5365,
           -442.9212,   -719.3676,    454.6113,    573.3630,   -336.1842,
         -31278.8730,    276.9778,    253.2615,   2299.0779, -14371.6904],
        [   226.4721,  -1963.4968,    420.4904,   -984.8939,   -984.0728,
            176.4783,   -912.3080,   -769.9332,   -233.0477,  -1064.4044,
           -460.1212,   -674.6402,    457.5997,    617.6741,   -314.9187,
         -31252.0020,    281.0459,    218.1335,   2321.9182, -14413.5957],
        [   227.1148,  -1947.1757,    420.2562,   -979.1144,   -980.7831,
   

       grad_fn=<SliceBackward>)
tensor([[   252.2401,  -2276.0210,    462.9000,  -1174.6786,  -1166.7751,
            208.3435,  -1073.0924,   -913.4869,   -288.7988,  -1270.7422,
           -525.6546,   -785.2103,    546.6925,    667.4059,   -373.4396,
         -36493.8945,    326.0087,    324.8012,   2682.0112, -16835.3594],
        [   266.3044,  -2282.8579,    484.8882,  -1161.6465,  -1159.8428,
            199.5030,  -1070.7365,   -911.8447,   -272.4117,  -1275.8525,
           -534.9347,   -775.2842,    559.0588,    702.1714,   -349.5705,
         -36531.5977,    346.7591,    317.8488,   2742.9543, -16860.4727],
        [   262.1917,  -2276.1011,    497.5944,  -1141.6765,  -1144.1954,
            204.8273,  -1062.6772,   -894.9814,   -279.5482,  -1255.0675,
           -559.2006,   -794.0677,    518.3138,    654.3866,   -373.0516,
         -36493.8945,    337.0604,    288.7460,   2689.6633, -16813.1816],
        [   264.2277,  -2276.0217,    491.5350,  -1151.3293,  -1162.0624,
   

       grad_fn=<SliceBackward>)
tensor([[   245.5102,  -2066.2869,    441.4960,  -1041.4127,  -1044.4679,
            196.0062,   -952.1653,   -805.5598,   -249.7269,  -1145.3604,
           -496.0793,   -697.6417,    507.4867,    643.4001,   -334.5049,
         -33159.6406,    329.1179,    299.5010,   2473.7622, -15262.5059],
        [   231.5693,  -2086.9763,    442.6470,  -1041.0314,  -1040.0204,
            187.6967,   -978.2839,   -804.8820,   -254.4529,  -1119.1820,
           -497.8188,   -760.7763,    441.6937,    616.1443,   -395.2896,
         -33186.0273,    261.1209,    239.4796,   2457.1147, -15249.8604],
        [   236.2572,  -2066.1990,    447.2145,  -1043.5039,  -1042.4742,
            178.6231,   -961.1443,   -808.0319,   -249.8027,  -1145.0922,
           -464.7789,   -706.8174,    498.9558,    627.9871,   -330.7534,
         -33171.9453,    315.7969,    279.5128,   2476.8909, -15257.1621],
        [   246.8284,  -2068.8186,    448.3613,  -1037.5549,  -1039.7411,
   

...

       grad_fn=<SliceBackward>)
tensor([[   249.8220,  -2147.5564,    464.1002,  -1076.4045,  -1088.4141,
            208.1954,   -997.1558,   -851.7267,   -260.9294,  -1171.7133,
           -499.9639,   -718.9974,    479.2518,    662.8881,   -365.0076,
         -34425.6641,    341.8017,    288.8731,   2556.2468, -15848.3037],
        [   261.4465,  -2147.3677,    462.4956,  -1075.7020,  -1086.4032,
            185.9569,   -991.7621,   -833.6725,   -261.4784,  -1167.9420,
           -482.9765,   -748.1237,    484.3596,    634.2493,   -365.9907,
         -34476.0469,    351.1724,    280.1098,   2574.4978, -15881.5576],
        [   222.9190,  -2147.0120,    450.2159,  -1098.9714,  -1102.8721,
            199.7764,  -1012.1143,   -857.7698,   -270.7538,  -1176.5057,
           -482.9765,   -774.7062,    491.0293,    629.0596,   -355.0648,
         -34456.9414,    336.7759,    257.9755,   2535.9731, -15879.8828],
        [   255.2952,  -2153.4773,    453.9247,  -1085.4348,  -1085.3104,
   

       grad_fn=<SliceBackward>)
tensor([[   238.2827,  -1952.7703,    415.7517,   -983.5386,  -1001.2811,
            171.2032,   -907.7108,   -775.1841,   -240.4929,  -1077.0461,
           -439.2810,   -667.9501,    457.1126,    607.6634,   -302.6385,
         -31324.2266,    319.3136,    255.5618,   2343.3584, -14432.3691],
        [   234.2459,  -1956.8527,    411.2516,   -994.2512,   -996.7510,
            154.5562,   -921.6483,   -767.6320,   -233.7385,  -1075.4847,
           -443.6175,   -697.0070,    449.9430,    589.1513,   -297.5622,
         -31326.2285,    278.4695,    248.6484,   2338.5935, -14413.2900],
        [   193.8784,  -1954.9224,    402.3631,   -994.7672,  -1006.6289,
            169.0526,   -916.5671,   -788.3943,   -233.8449,  -1069.3076,
           -477.1770,   -647.9432,    460.1386,    589.9460,   -300.7752,
         -31310.8496,    320.6320,    256.4507,   2354.2996, -14435.0986],
        [   229.5142,  -1956.9657,    425.5692,   -972.0530,   -984.3342,
   

       grad_fn=<SliceBackward>)
tensor([[   201.1881,  -1736.0299,    364.0055,   -871.7817,   -878.5521,
            165.2460,   -818.8150,   -681.2736,   -206.9348,   -945.1573,
           -412.3921,   -587.2404,    415.0928,    515.0465,   -280.2729,
         -27732.3125,    283.1076,    254.2473,   2077.6111, -12789.9951],
        [   200.2000,  -1737.5787,    356.4962,   -870.1688,   -886.1783,
            144.9014,   -809.3004,   -694.6570,   -206.8886,   -963.5540,
           -423.5653,   -566.1221,    391.8006,    522.7782,   -281.6803,
         -27763.5645,    247.5490,    223.7977,   2090.2063, -12759.5625],
        [   201.9796,  -1728.6450,    367.0566,   -877.5603,   -879.0610,
            157.8962,   -797.0120,   -692.1206,   -212.0391,   -953.5502,
           -412.1608,   -610.5000,    424.5883,    494.3247,   -282.3556,
         -27739.2227,    266.5244,    234.8898,   2066.4736, -12764.8916],
        [   186.8337,  -1732.4044,    353.8929,   -893.5322,   -879.1777,
   

       grad_fn=<SliceBackward>)
tensor([[   247.7924,  -2148.9224,    456.7293,  -1079.4464,  -1080.1251,
            192.2506,   -994.2066,   -830.0506,   -259.6368,  -1189.4271,
           -491.4715,   -720.6614,    515.5589,    653.8857,   -343.4407,
         -34354.6992,    349.0094,    283.4201,   2544.6174, -15801.8545],
        [   238.7285,  -2140.9917,    468.0664,  -1096.3333,  -1092.6160,
            186.7127,  -1007.8721,   -856.9346,   -270.9713,  -1191.6039,
           -492.6072,   -720.5383,    514.7180,    669.5156,   -312.7105,
         -34354.4414,    342.2998,    300.5651,   2565.1880, -15802.6680],
        [   264.3668,  -2142.0217,    457.3391,  -1069.1611,  -1084.1562,
            187.3584,  -1002.0636,   -840.9276,   -256.6319,  -1177.3911,
           -506.9268,   -742.0876,    525.8689,    644.8766,   -352.6788,
         -34352.9805,    329.5094,    287.8048,   2541.9277, -15835.0439],
        [   253.8006,  -2146.3618,    455.3446,  -1079.6980,  -1088.6964,
   

       grad_fn=<SliceBackward>)
tensor([[   262.9854,  -2147.1655,    462.4144,  -1088.4069,  -1086.3250,
            200.4730,   -997.2990,   -846.0128,   -259.5544,  -1185.8732,
           -502.5182,   -707.3207,    527.3882,    647.7526,   -331.0037,
         -34434.1641,    324.4930,    285.0495,   2578.2383, -15868.6240],
        [   251.0264,  -2147.1040,    447.1369,  -1096.6678,  -1083.9916,
            191.1213,  -1016.4521,   -860.6552,   -261.0105,  -1183.1039,
           -482.9933,   -761.8110,    489.4067,    596.9271,   -373.1129,
         -34454.3984,    379.1358,    299.2076,   2577.5215, -15887.7188],
        [   227.7173,  -2154.3491,    457.1778,  -1084.2084,  -1086.5486,
            191.9857,   -996.3170,   -834.4264,   -257.1233,  -1188.6134,
           -540.0077,   -735.6863,    452.5544,    681.1035,   -373.0417,
         -34487.0781,    312.4873,    280.0134,   2559.2949, -15889.7812],
        [   247.7744,  -2147.2678,    469.4284,  -1093.7537,  -1098.4985,
   

In [ ]:
# number of epochs 
epochs = 85

model.train() # prep model for training

for epoch in range(epochs):
    
    train_loss = 0.0
    total = 0.0
    
    for data, target in train_loader:
        optimizer.zero_grad()
        output = model(data)        
        loss = criterion(output, target)
        loss.backward()
        optimizer.step()
        train_loss += loss.item()*data.size(0)
        total += len(data) 
        
    # print training statistics 
    # calculate average loss over an epoch
    train_loss = train_loss/total
    print('Epoch: {} \tTraining Loss: {:.6f}'.format(epoch+1,train_loss))
    

In [ ]:
correct = 0.0
test_loss = 0.0
total= 0.0

model.eval() # prep model for evaluation

for data, target in test_loader:
    output = model(data)
    loss = criterion(output, target)  
    test_loss += loss.item()*data.size(0)
    _, pred = torch.max(output, 1)
    correct += np.squeeze(pred.eq(target.data.view_as(pred))).sum()
    total += len(data)
    
# calculate and print average test loss
test_loss = test_loss/total
print('Test Loss: {:.6f}'.format(test_loss)) 

# calculate and print accuracy
print('Test Accuracy: {:.2f}% ({}/{})' .format(100. * np.float(correct) / total, 
                                           correct, total))
        


In [ ]:
test_data = pd.read_csv('../input/test.csv')
test_data = torch.from_numpy(test_data.values.reshape(-1,1,28,28))
test_data = test_data.type(torch.float)

In [ ]:
model.eval() 
result = []

for data in test_data:
    # forward pass: compute predicted outputs by passing inputs to the model
    output = model(data)
    _, pred = torch.max(output, 1)
    pred = pred.numpy()
    result += pred.tolist()

results = pd.Series(result,name="Label")
Imageld = pd.Series(range(1,len(result)+1),name="Imageld")

submission = pd.concat([Imageld,results],axis = 1)
submission.to_csv("submission.csv",index=False)

In [ ]:
x = pd.read_csv('submission.csv')
print(x[:10])